In [88]:
import os
import numpy as np
import SimpleITK as sitk
import cv2

In [89]:
data_name = "_.nii.gz"
mask_name = "_.nii.gz"

In [92]:
data_path = r"../database/Brast/"

In [91]:
dataa_path = r"../database/Brast/"

In [82]:
outputImg_path = r"./seven/data"

In [81]:
outputMask_path = r"./seven/label"

In [84]:
if not os.path.exists(outputImg_path):
    os.mkdir(outputImg_path)
if not os.path.exists(outputMask_path):
    os.mkdir(outputMask_path)

In [93]:
def file_name_path(file_dir, dir=True, file=False):
    """
    get root path,sub_dirs,all_sub_files
    :param file_dir:
    :return: dir or file
    """
    mri_list = os.listdir(file_dir)
    seg_list = list(map(lambda x: x.replace('volume', 'segmentation').replace('.nii.gz', '.nii'), mri_list))

    mri_list = list(map(lambda x: os.path.join(file_dir, x), mri_list))
    seg_list = list(map(lambda x: os.path.join(bratslgg_path, x), seg_list))
    return mri_list , seg_list

In [103]:
pathmri_list,pathmask_list = data_name_path(data_path)
print(len(pathmri_list))
print("------------")
print(len(pathmask_list))


23
------------
23


In [79]:
def normalize(slice, bottom=99, down=1):
    """
    normalize image with mean and std for regionnonzero,and clip the value into range
    :param slice:
    :param bottom:
    :param down:
    :return:
    """
    
    b = np.percentile(slice, bottom)
    t = np.percentile(slice, down)
    slice = np.clip(slice, t, b)#限定范围numpy.clip(a, a_min, a_max, out=None)

    image_nonzero = slice[np.nonzero(slice)]
    if np.std(slice) == 0 or np.std(image_nonzero) == 0:
        return slice
    else:
        tmp = (slice - np.mean(image_nonzero)) / np.std(image_nonzero)
        
        tmp[tmp == tmp.min()] = -9 #黑色背景区域
        return tmp

np.percentil
分位数:
在我们中学就有过中位数，其实中位数就是一个二分位数，取中位数左边区间的值的概率等于取其右边区间的值的概率。另外在大学的概率论课程中，另一个比较常见的是四分位数，也就是25%,50%,75%这三个切分点。
分位数意义：表示了在这个样本集中从小至大排列之后小于某值的样本子集占总样本集的比例
我采用了99与1这两个分位数来作为鉴定outliers分布的界限从而进行异常值的修正。这样子的修正可以以更好的准确率来得到我们理想的数据集。
有点像去掉最低分去掉最高分的意思

In [104]:
sum = 0
a=0

for subsetindex in range(len(pathmri_list)):
    mask_image = pathmask_list[subsetindex]
    mask = sitk.ReadImage(mask_image, sitk.sitkUInt8) 
    mask_array = sitk.GetArrayFromImage(mask)
    print(mask_array.shape)
    sum_lin = np.count_nonzero(mask_array)
    a = 155*240*240
    sing_averge = sum_lin/a
    sum = sum + sing_averge
avg = sum/len(pathmri_list)
print(avg)
print("Done！")
  

(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
(155, 240, 240)
0.013651117149758456
Done！


In [12]:
#五通道叠加
for subsetindex in range(len(pathmri_list)):
    data_image = pathmri_list[subsetindex]
    mask_image = pathmask_list[subsetindex]
    #获取每个病例的四个模态及Mask数据
    data_src = sitk.ReadImage(data_image, sitk.sitkInt16)
    mask = sitk.ReadImage(mask_image, sitk.sitkUInt8)
    #GetArrayFromImage()可用于将SimpleITK对象转换为ndarray
    data_array = sitk.GetArrayFromImage(data_src)
    mask_array = sitk.GetArrayFromImage(mask)
    #对四个模态分别进行标准化,由于它们对比度不同
    data_array_nor = normalize(data_array)
    for index in range(0,90):
        print(index)
        index_1 = index - 1
        index_1_2 = index - 2
        index_2 = index + 1
        index_2_2 = index + 2
        if (index == 0):
            FiveImageArray = cv2.merge([data_array_nor[2],data_array_nor[1],data_array_nor[0],data_array_nor[1],data_array_nor[2]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,FiveImageArray)#(160,160,4) np.float dtype('float64')
        if (index == 1):
            FiveImageArray = cv2.merge([data_array_nor[1],data_array_nor[0],data_array_nor[1],data_array_nor[2],data_array_nor[3]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,FiveImageArray)#(160,160,4) np.float dtype('float64')
        if (index == 88):
            FiveImageArray = cv2.merge([data_array_nor[86],data_array_nor[87],data_array_nor[88],data_array_nor[89],data_array_nor[88]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,FiveImageArray)#(160,160,4) np.float dtype('float64')
        elif (index == 89):
            FiveImageArray = cv2.merge([data_array_nor[87],data_array_nor[88],data_array_nor[89],data_array_nor[88],data_array_nor[87]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,FiveImageArray)
        else:
            FiveImageArray = cv2.merge([data_array_nor[index_1_2],data_array_nor[index_1],data_array_nor[index],flair_array_nor[index_2],data_array_nor[index_2_2]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,FiveImageArray)
        maskpath = outputMask_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
        maskImg = mask_array[index,:,:]
        if np.max(maskImg) !=0:
            np.save(maskpath,maskImg)

print("Done！")
        
    

0
(512, 512, 5)
./LiTS/data//0_0.npy
(512, 512, 5)
./LiTS/data//0_0.npy
(512, 512)
maskpath ./LiTS/label//0_0.npy
1
(512, 512, 5)
./LiTS/data//0_1.npy
(512, 512, 5)
./LiTS/data//0_1.npy
(512, 512)
maskpath ./LiTS/label//0_1.npy
2
(512, 512, 5)
./LiTS/data//0_2.npy
(512, 512)
maskpath ./LiTS/label//0_2.npy
3
(512, 512, 5)
./LiTS/data//0_3.npy
(512, 512)
maskpath ./LiTS/label//0_3.npy
4
(512, 512, 5)
./LiTS/data//0_4.npy
(512, 512)
maskpath ./LiTS/label//0_4.npy
5
(512, 512, 5)
./LiTS/data//0_5.npy
(512, 512)
maskpath ./LiTS/label//0_5.npy
6
(512, 512, 5)
./LiTS/data//0_6.npy
(512, 512)
maskpath ./LiTS/label//0_6.npy
7
(512, 512, 5)
./LiTS/data//0_7.npy
(512, 512)
maskpath ./LiTS/label//0_7.npy
8
(512, 512, 5)
./LiTS/data//0_8.npy
(512, 512)
maskpath ./LiTS/label//0_8.npy
9
(512, 512, 5)
./LiTS/data//0_9.npy
(512, 512)
maskpath ./LiTS/label//0_9.npy
10
(512, 512, 5)
./LiTS/data//0_10.npy
(512, 512)
maskpath ./LiTS/label//0_10.npy
11
(512, 512, 5)
./LiTS/data//0_11.npy
(512, 512)
maskpath

(512, 512)
maskpath ./LiTS/label//1_43.npy
44
(512, 512, 5)
./LiTS/data//1_44.npy
(512, 512)
maskpath ./LiTS/label//1_44.npy
45
(512, 512, 5)
./LiTS/data//1_45.npy
(512, 512)
maskpath ./LiTS/label//1_45.npy
46
(512, 512, 5)
./LiTS/data//1_46.npy
(512, 512)
maskpath ./LiTS/label//1_46.npy
47
(512, 512, 5)
./LiTS/data//1_47.npy
(512, 512)
maskpath ./LiTS/label//1_47.npy
48
(512, 512, 5)
./LiTS/data//1_48.npy
(512, 512)
maskpath ./LiTS/label//1_48.npy
49
(512, 512, 5)
./LiTS/data//1_49.npy
(512, 512)
maskpath ./LiTS/label//1_49.npy
50
(512, 512, 5)
./LiTS/data//1_50.npy
(512, 512)
maskpath ./LiTS/label//1_50.npy
51
(512, 512, 5)
./LiTS/data//1_51.npy
(512, 512)
maskpath ./LiTS/label//1_51.npy
52
(512, 512, 5)
./LiTS/data//1_52.npy
(512, 512)
maskpath ./LiTS/label//1_52.npy
53
(512, 512, 5)
./LiTS/data//1_53.npy
(512, 512)
maskpath ./LiTS/label//1_53.npy
54
(512, 512, 5)
./LiTS/data//1_54.npy
(512, 512)
maskpath ./LiTS/label//1_54.npy
55
(512, 512, 5)
./LiTS/data//1_55.npy
(512, 512)
maskp

(512, 512)
maskpath ./LiTS/label//2_67.npy
68
(512, 512, 5)
./LiTS/data//2_68.npy
(512, 512)
maskpath ./LiTS/label//2_68.npy
69
(512, 512, 5)
./LiTS/data//2_69.npy
(512, 512)
maskpath ./LiTS/label//2_69.npy
70
(512, 512, 5)
./LiTS/data//2_70.npy
(512, 512)
maskpath ./LiTS/label//2_70.npy
71
(512, 512, 5)
./LiTS/data//2_71.npy
(512, 512)
maskpath ./LiTS/label//2_71.npy
72
(512, 512, 5)
./LiTS/data//2_72.npy
(512, 512)
maskpath ./LiTS/label//2_72.npy
73
(512, 512, 5)
./LiTS/data//2_73.npy
(512, 512)
maskpath ./LiTS/label//2_73.npy
74
(512, 512, 5)
./LiTS/data//2_74.npy
(512, 512)
maskpath ./LiTS/label//2_74.npy
75
(512, 512, 5)
./LiTS/data//2_75.npy
(512, 512)
maskpath ./LiTS/label//2_75.npy
76
(512, 512, 5)
./LiTS/data//2_76.npy
(512, 512)
maskpath ./LiTS/label//2_76.npy
77
(512, 512, 5)
./LiTS/data//2_77.npy
(512, 512)
maskpath ./LiTS/label//2_77.npy
78
(512, 512, 5)
./LiTS/data//2_78.npy
(512, 512)
maskpath ./LiTS/label//2_78.npy
79
(512, 512, 5)
./LiTS/data//2_79.npy
(512, 512)
maskp

0
(512, 512, 5)
./LiTS/data//4_0.npy
(512, 512, 5)
./LiTS/data//4_0.npy
(512, 512)
maskpath ./LiTS/label//4_0.npy
1
(512, 512, 5)
./LiTS/data//4_1.npy
(512, 512, 5)
./LiTS/data//4_1.npy
(512, 512)
maskpath ./LiTS/label//4_1.npy
2
(512, 512, 5)
./LiTS/data//4_2.npy
(512, 512)
maskpath ./LiTS/label//4_2.npy
3
(512, 512, 5)
./LiTS/data//4_3.npy
(512, 512)
maskpath ./LiTS/label//4_3.npy
4
(512, 512, 5)
./LiTS/data//4_4.npy
(512, 512)
maskpath ./LiTS/label//4_4.npy
5
(512, 512, 5)
./LiTS/data//4_5.npy
(512, 512)
maskpath ./LiTS/label//4_5.npy
6
(512, 512, 5)
./LiTS/data//4_6.npy
(512, 512)
maskpath ./LiTS/label//4_6.npy
7
(512, 512, 5)
./LiTS/data//4_7.npy
(512, 512)
maskpath ./LiTS/label//4_7.npy
8
(512, 512, 5)
./LiTS/data//4_8.npy
(512, 512)
maskpath ./LiTS/label//4_8.npy
9
(512, 512, 5)
./LiTS/data//4_9.npy
(512, 512)
maskpath ./LiTS/label//4_9.npy
10
(512, 512, 5)
./LiTS/data//4_10.npy
(512, 512)
maskpath ./LiTS/label//4_10.npy
11
(512, 512, 5)
./LiTS/data//4_11.npy
(512, 512)
maskpath

(512, 512, 5)
./LiTS/data//5_53.npy
(512, 512)
maskpath ./LiTS/label//5_53.npy
54
(512, 512, 5)
./LiTS/data//5_54.npy
(512, 512)
maskpath ./LiTS/label//5_54.npy
55
(512, 512, 5)
./LiTS/data//5_55.npy
(512, 512)
maskpath ./LiTS/label//5_55.npy
56
(512, 512, 5)
./LiTS/data//5_56.npy
(512, 512)
maskpath ./LiTS/label//5_56.npy
57
(512, 512, 5)
./LiTS/data//5_57.npy
(512, 512)
maskpath ./LiTS/label//5_57.npy
58
(512, 512, 5)
./LiTS/data//5_58.npy
(512, 512)
maskpath ./LiTS/label//5_58.npy
59
(512, 512, 5)
./LiTS/data//5_59.npy
(512, 512)
maskpath ./LiTS/label//5_59.npy
60
(512, 512, 5)
./LiTS/data//5_60.npy
(512, 512)
maskpath ./LiTS/label//5_60.npy
61
(512, 512, 5)
./LiTS/data//5_61.npy
(512, 512)
maskpath ./LiTS/label//5_61.npy
62
(512, 512, 5)
./LiTS/data//5_62.npy
(512, 512)
maskpath ./LiTS/label//5_62.npy
63
(512, 512, 5)
./LiTS/data//5_63.npy
(512, 512)
maskpath ./LiTS/label//5_63.npy
64
(512, 512, 5)
./LiTS/data//5_64.npy
(512, 512)
maskpath ./LiTS/label//5_64.npy
65
(512, 512, 5)
./

...

(512, 512)
maskpath ./LiTS/label//22_66.npy
67
(512, 512, 5)
./LiTS/data//22_67.npy
(512, 512)
maskpath ./LiTS/label//22_67.npy
68
(512, 512, 5)
./LiTS/data//22_68.npy
(512, 512)
maskpath ./LiTS/label//22_68.npy
69
(512, 512, 5)
./LiTS/data//22_69.npy
(512, 512)
maskpath ./LiTS/label//22_69.npy
70
(512, 512, 5)
./LiTS/data//22_70.npy
(512, 512)
maskpath ./LiTS/label//22_70.npy
71
(512, 512, 5)
./LiTS/data//22_71.npy
(512, 512)
maskpath ./LiTS/label//22_71.npy
72
(512, 512, 5)
./LiTS/data//22_72.npy
(512, 512)
maskpath ./LiTS/label//22_72.npy
73
(512, 512, 5)
./LiTS/data//22_73.npy
(512, 512)
maskpath ./LiTS/label//22_73.npy
74
(512, 512, 5)
./LiTS/data//22_74.npy
(512, 512)
maskpath ./LiTS/label//22_74.npy
75
(512, 512, 5)
./LiTS/data//22_75.npy
(512, 512)
maskpath ./LiTS/label//22_75.npy
76
(512, 512, 5)
./LiTS/data//22_76.npy
(512, 512)
maskpath ./LiTS/label//22_76.npy
77
(512, 512, 5)
./LiTS/data//22_77.npy
(512, 512)
maskpath ./LiTS/label//22_77.npy
78
(512, 512, 5)
./LiTS/data//22

0
(512, 512, 5)
./LiTS/data//24_0.npy
(512, 512, 5)
./LiTS/data//24_0.npy
(512, 512)
maskpath ./LiTS/label//24_0.npy
1
(512, 512, 5)
./LiTS/data//24_1.npy
(512, 512, 5)
./LiTS/data//24_1.npy
(512, 512)
maskpath ./LiTS/label//24_1.npy
2
(512, 512, 5)
./LiTS/data//24_2.npy
(512, 512)
maskpath ./LiTS/label//24_2.npy
3
(512, 512, 5)
./LiTS/data//24_3.npy
(512, 512)
maskpath ./LiTS/label//24_3.npy
4
(512, 512, 5)
./LiTS/data//24_4.npy
(512, 512)
maskpath ./LiTS/label//24_4.npy
5
(512, 512, 5)
./LiTS/data//24_5.npy
(512, 512)
maskpath ./LiTS/label//24_5.npy
6
(512, 512, 5)
./LiTS/data//24_6.npy
(512, 512)
maskpath ./LiTS/label//24_6.npy
7
(512, 512, 5)
./LiTS/data//24_7.npy
(512, 512)
maskpath ./LiTS/label//24_7.npy
8
(512, 512, 5)
./LiTS/data//24_8.npy
(512, 512)
maskpath ./LiTS/label//24_8.npy
9
(512, 512, 5)
./LiTS/data//24_9.npy
(512, 512)
maskpath ./LiTS/label//24_9.npy
10
(512, 512, 5)
./LiTS/data//24_10.npy
(512, 512)
maskpath ./LiTS/label//24_10.npy
11
(512, 512, 5)
./LiTS/data//24_1

(512, 512)
maskpath ./LiTS/label//25_67.npy
68
(512, 512, 5)
./LiTS/data//25_68.npy
(512, 512)
maskpath ./LiTS/label//25_68.npy
69
(512, 512, 5)
./LiTS/data//25_69.npy
(512, 512)
maskpath ./LiTS/label//25_69.npy
70
(512, 512, 5)
./LiTS/data//25_70.npy
(512, 512)
maskpath ./LiTS/label//25_70.npy
71
(512, 512, 5)
./LiTS/data//25_71.npy
(512, 512)
maskpath ./LiTS/label//25_71.npy
72
(512, 512, 5)
./LiTS/data//25_72.npy
(512, 512)
maskpath ./LiTS/label//25_72.npy
73
(512, 512, 5)
./LiTS/data//25_73.npy
(512, 512)
maskpath ./LiTS/label//25_73.npy
74
(512, 512, 5)
./LiTS/data//25_74.npy
(512, 512)
maskpath ./LiTS/label//25_74.npy
75
(512, 512, 5)
./LiTS/data//25_75.npy
(512, 512)
maskpath ./LiTS/label//25_75.npy
76
(512, 512, 5)
./LiTS/data//25_76.npy
(512, 512)
maskpath ./LiTS/label//25_76.npy
77
(512, 512, 5)
./LiTS/data//25_77.npy
(512, 512)
maskpath ./LiTS/label//25_77.npy
78
(512, 512, 5)
./LiTS/data//25_78.npy
(512, 512)
maskpath ./LiTS/label//25_78.npy
79
(512, 512, 5)
./LiTS/data//25

0
(512, 512, 5)
./LiTS/data//27_0.npy
(512, 512, 5)
./LiTS/data//27_0.npy
(512, 512)
maskpath ./LiTS/label//27_0.npy
1
(512, 512, 5)
./LiTS/data//27_1.npy
(512, 512, 5)
./LiTS/data//27_1.npy
(512, 512)
maskpath ./LiTS/label//27_1.npy
2
(512, 512, 5)
./LiTS/data//27_2.npy
(512, 512)
maskpath ./LiTS/label//27_2.npy
3
(512, 512, 5)
./LiTS/data//27_3.npy
(512, 512)
maskpath ./LiTS/label//27_3.npy
4
(512, 512, 5)
./LiTS/data//27_4.npy
(512, 512)
maskpath ./LiTS/label//27_4.npy
5
(512, 512, 5)
./LiTS/data//27_5.npy
(512, 512)
maskpath ./LiTS/label//27_5.npy
6
(512, 512, 5)
./LiTS/data//27_6.npy
(512, 512)
maskpath ./LiTS/label//27_6.npy
7
(512, 512, 5)
./LiTS/data//27_7.npy
(512, 512)
maskpath ./LiTS/label//27_7.npy
8
(512, 512, 5)
./LiTS/data//27_8.npy
(512, 512)
maskpath ./LiTS/label//27_8.npy
9
(512, 512, 5)
./LiTS/data//27_9.npy
(512, 512)
maskpath ./LiTS/label//27_9.npy
10
(512, 512, 5)
./LiTS/data//27_10.npy
(512, 512)
maskpath ./LiTS/label//27_10.npy
11
(512, 512, 5)
./LiTS/data//27_1

RuntimeError: Exception thrown in SimpleITK ImageFileReader_Execute: /tmp/SimpleITK/Code/IO/src/sitkImageReaderBase.cxx:97:
sitk::ERROR: The file "../database/reLiTS/label/segmentation-121.nii" does not exist.

In [15]:
#三通道叠加
for subsetindex in range(len(pathmri_list)):
    #获取每个病例的四个模态及Mask的路径
    flair_image = pathmri_list[subsetindex]
    mask_image = pathmask_list[subsetindex]
    #获取每个病例的四个模态及Mask数据
    flair_src = sitk.ReadImage(flair_image, sitk.sitkInt16)
    mask = sitk.ReadImage(mask_image, sitk.sitkUInt8)
    #GetArrayFromImage()可用于将SimpleITK对象转换为ndarray
    flair_array = sitk.GetArrayFromImage(flair_src)
    mask_array = sitk.GetArrayFromImage(mask)
    #对四个模态分别进行标准化,由于它们对比度不同
    flair_array_nor = normalize(flair_array)
    #叠加三通道：
    #ThreeImageArray = []
    for index in range(0,90):
        index_1 = index - 1
        index_2 = index + 1
        if (index == 0):
            ThreeImageArray = cv2.merge([flair_array_nor[1],flair_array_nor[0],flair_array_nor[1]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
        elif (index == 89):
            ThreeImageArray = cv2.merge([flair_array_nor[88],flair_array_nor[89],flair_array_nor[88]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,ThreeImageArray)
        else:
            ThreeImageArray = cv2.merge([flair_array_nor[index_1],flair_array_nor[index],flair_array_nor[index_2]])
            imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
            if np.max(mask_array[index,:,:]) != 0:
                np.save(imagepath,ThreeImageArray)
        maskpath = outputMask_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
        maskImg = mask_array[index,:,:]
        if np.max(maskImg) !=0:
            np.save(maskpath,maskImg)


print("Done！")
        
    

0
(512, 512, 3)
./three/data//0_0.npy
(512, 512)
maskpath ./three/label//0_0.npy
1
(512, 512, 3)
./three/data//0_1.npy
(512, 512)
maskpath ./three/label//0_1.npy
2
(512, 512, 3)
./three/data//0_2.npy
(512, 512)
maskpath ./three/label//0_2.npy
3
(512, 512, 3)
./three/data//0_3.npy
(512, 512)
maskpath ./three/label//0_3.npy
4
(512, 512, 3)
./three/data//0_4.npy
(512, 512)
maskpath ./three/label//0_4.npy
5
(512, 512, 3)
./three/data//0_5.npy
(512, 512)
maskpath ./three/label//0_5.npy
6
(512, 512, 3)
./three/data//0_6.npy
(512, 512)
maskpath ./three/label//0_6.npy
7
(512, 512, 3)
./three/data//0_7.npy
(512, 512)
maskpath ./three/label//0_7.npy
8
(512, 512, 3)
./three/data//0_8.npy
(512, 512)
maskpath ./three/label//0_8.npy
9
(512, 512, 3)
./three/data//0_9.npy
(512, 512)
maskpath ./three/label//0_9.npy
10
(512, 512, 3)
./three/data//0_10.npy
(512, 512)
maskpath ./three/label//0_10.npy
11
(512, 512, 3)
./three/data//0_11.npy
(512, 512)
maskpath ./three/label//0_11.npy
12
(512, 512, 3)
./thr

74
(512, 512, 3)
./three/data//1_74.npy
(512, 512)
maskpath ./three/label//1_74.npy
75
(512, 512, 3)
./three/data//1_75.npy
(512, 512)
maskpath ./three/label//1_75.npy
76
(512, 512, 3)
./three/data//1_76.npy
(512, 512)
maskpath ./three/label//1_76.npy
77
(512, 512, 3)
./three/data//1_77.npy
(512, 512)
maskpath ./three/label//1_77.npy
78
(512, 512, 3)
./three/data//1_78.npy
(512, 512)
maskpath ./three/label//1_78.npy
79
(512, 512, 3)
./three/data//1_79.npy
(512, 512)
maskpath ./three/label//1_79.npy
80
(512, 512, 3)
./three/data//1_80.npy
(512, 512)
maskpath ./three/label//1_80.npy
81
(512, 512, 3)
./three/data//1_81.npy
(512, 512)
maskpath ./three/label//1_81.npy
82
(512, 512, 3)
./three/data//1_82.npy
(512, 512)
maskpath ./three/label//1_82.npy
83
(512, 512, 3)
./three/data//1_83.npy
(512, 512)
maskpath ./three/label//1_83.npy
84
(512, 512, 3)
./three/data//1_84.npy
(512, 512)
maskpath ./three/label//1_84.npy
85
(512, 512, 3)
./three/data//1_85.npy
(512, 512)
maskpath ./three/label//1

0
(512, 512, 3)
./three/data//3_0.npy
(512, 512)
maskpath ./three/label//3_0.npy
1
(512, 512, 3)
./three/data//3_1.npy
(512, 512)
maskpath ./three/label//3_1.npy
2
(512, 512, 3)
./three/data//3_2.npy
(512, 512)
maskpath ./three/label//3_2.npy
3
(512, 512, 3)
./three/data//3_3.npy
(512, 512)
maskpath ./three/label//3_3.npy
4
(512, 512, 3)
./three/data//3_4.npy
(512, 512)
maskpath ./three/label//3_4.npy
5
(512, 512, 3)
./three/data//3_5.npy
(512, 512)
maskpath ./three/label//3_5.npy
6
(512, 512, 3)
./three/data//3_6.npy
(512, 512)
maskpath ./three/label//3_6.npy
7
(512, 512, 3)
./three/data//3_7.npy
(512, 512)
maskpath ./three/label//3_7.npy
8
(512, 512, 3)
./three/data//3_8.npy
(512, 512)
maskpath ./three/label//3_8.npy
9
(512, 512, 3)
./three/data//3_9.npy
(512, 512)
maskpath ./three/label//3_9.npy
10
(512, 512, 3)
./three/data//3_10.npy
(512, 512)
maskpath ./three/label//3_10.npy
11
(512, 512, 3)
./three/data//3_11.npy
(512, 512)
maskpath ./three/label//3_11.npy
12
(512, 512, 3)
./thr

(512, 512)
maskpath ./three/label//4_50.npy
51
(512, 512, 3)
./three/data//4_51.npy
(512, 512)
maskpath ./three/label//4_51.npy
52
(512, 512, 3)
./three/data//4_52.npy
(512, 512)
maskpath ./three/label//4_52.npy
53
(512, 512, 3)
./three/data//4_53.npy
(512, 512)
maskpath ./three/label//4_53.npy
54
(512, 512, 3)
./three/data//4_54.npy
(512, 512)
maskpath ./three/label//4_54.npy
55
(512, 512, 3)
./three/data//4_55.npy
(512, 512)
maskpath ./three/label//4_55.npy
56
(512, 512, 3)
./three/data//4_56.npy
(512, 512)
maskpath ./three/label//4_56.npy
57
(512, 512, 3)
./three/data//4_57.npy
(512, 512)
maskpath ./three/label//4_57.npy
58
(512, 512, 3)
./three/data//4_58.npy
(512, 512)
maskpath ./three/label//4_58.npy
59
(512, 512, 3)
./three/data//4_59.npy
(512, 512)
maskpath ./three/label//4_59.npy
60
(512, 512, 3)
./three/data//4_60.npy
(512, 512)
maskpath ./three/label//4_60.npy
61
(512, 512, 3)
./three/data//4_61.npy
(512, 512)
maskpath ./three/label//4_61.npy
62
(512, 512, 3)
./three/data//4

(512, 512)
maskpath ./three/label//5_88.npy
89
(512, 512, 3)
./three/data//5_89.npy
(512, 512)
maskpath ./three/label//5_89.npy
0
(512, 512, 3)
./three/data//6_0.npy
(512, 512)
maskpath ./three/label//6_0.npy
1
(512, 512, 3)
./three/data//6_1.npy
(512, 512)
maskpath ./three/label//6_1.npy
2
(512, 512, 3)
./three/data//6_2.npy
(512, 512)
maskpath ./three/label//6_2.npy
3
(512, 512, 3)
./three/data//6_3.npy
(512, 512)
maskpath ./three/label//6_3.npy
4
(512, 512, 3)
./three/data//6_4.npy
(512, 512)
maskpath ./three/label//6_4.npy
5
(512, 512, 3)
./three/data//6_5.npy
(512, 512)
maskpath ./three/label//6_5.npy
6
(512, 512, 3)
./three/data//6_6.npy
(512, 512)
maskpath ./three/label//6_6.npy
7
(512, 512, 3)
./three/data//6_7.npy
(512, 512)
maskpath ./three/label//6_7.npy
8
(512, 512, 3)
./three/data//6_8.npy
(512, 512)
maskpath ./three/label//6_8.npy
9
(512, 512, 3)
./three/data//6_9.npy
(512, 512)
maskpath ./three/label//6_9.npy
10
(512, 512, 3)
./three/data//6_10.npy
(512, 512)
maskpath ./

...

(512, 512)
maskpath ./three/label//351_78.npy
79
(512, 512, 3)
./three/data//351_79.npy
(512, 512)
maskpath ./three/label//351_79.npy
80
(512, 512, 3)
./three/data//351_80.npy
(512, 512)
maskpath ./three/label//351_80.npy
81
(512, 512, 3)
./three/data//351_81.npy
(512, 512)
maskpath ./three/label//351_81.npy
82
(512, 512, 3)
./three/data//351_82.npy
(512, 512)
maskpath ./three/label//351_82.npy
83
(512, 512, 3)
./three/data//351_83.npy
(512, 512)
maskpath ./three/label//351_83.npy
84
(512, 512, 3)
./three/data//351_84.npy
(512, 512)
maskpath ./three/label//351_84.npy
85
(512, 512, 3)
./three/data//351_85.npy
(512, 512)
maskpath ./three/label//351_85.npy
86
(512, 512, 3)
./three/data//351_86.npy
(512, 512)
maskpath ./three/label//351_86.npy
87
(512, 512, 3)
./three/data//351_87.npy
(512, 512)
maskpath ./three/label//351_87.npy
88
(512, 512, 3)
./three/data//351_88.npy
(512, 512)
maskpath ./three/label//351_88.npy
89
(512, 512, 3)
./three/data//351_89.npy
(512, 512)
maskpath ./three/labe

0
(512, 512, 3)
./three/data//353_0.npy
(512, 512)
maskpath ./three/label//353_0.npy
1
(512, 512, 3)
./three/data//353_1.npy
(512, 512)
maskpath ./three/label//353_1.npy
2
(512, 512, 3)
./three/data//353_2.npy
(512, 512)
maskpath ./three/label//353_2.npy
3
(512, 512, 3)
./three/data//353_3.npy
(512, 512)
maskpath ./three/label//353_3.npy
4
(512, 512, 3)
./three/data//353_4.npy
(512, 512)
maskpath ./three/label//353_4.npy
5
(512, 512, 3)
./three/data//353_5.npy
(512, 512)
maskpath ./three/label//353_5.npy
6
(512, 512, 3)
./three/data//353_6.npy
(512, 512)
maskpath ./three/label//353_6.npy
7
(512, 512, 3)
./three/data//353_7.npy
(512, 512)
maskpath ./three/label//353_7.npy
8
(512, 512, 3)
./three/data//353_8.npy
(512, 512)
maskpath ./three/label//353_8.npy
9
(512, 512, 3)
./three/data//353_9.npy
(512, 512)
maskpath ./three/label//353_9.npy
10
(512, 512, 3)
./three/data//353_10.npy
(512, 512)
maskpath ./three/label//353_10.npy
11
(512, 512, 3)
./three/data//353_11.npy
(512, 512)
maskpath 

(512, 512)
maskpath ./three/label//354_58.npy
59
(512, 512, 3)
./three/data//354_59.npy
(512, 512)
maskpath ./three/label//354_59.npy
60
(512, 512, 3)
./three/data//354_60.npy
(512, 512)
maskpath ./three/label//354_60.npy
61
(512, 512, 3)
./three/data//354_61.npy
(512, 512)
maskpath ./three/label//354_61.npy
62
(512, 512, 3)
./three/data//354_62.npy
(512, 512)
maskpath ./three/label//354_62.npy
63
(512, 512, 3)
./three/data//354_63.npy
(512, 512)
maskpath ./three/label//354_63.npy
64
(512, 512, 3)
./three/data//354_64.npy
(512, 512)
maskpath ./three/label//354_64.npy
65
(512, 512, 3)
./three/data//354_65.npy
(512, 512)
maskpath ./three/label//354_65.npy
66
(512, 512, 3)
./three/data//354_66.npy
(512, 512)
maskpath ./three/label//354_66.npy
67
(512, 512, 3)
./three/data//354_67.npy
(512, 512)
maskpath ./three/label//354_67.npy
68
(512, 512, 3)
./three/data//354_68.npy
(512, 512)
maskpath ./three/label//354_68.npy
69
(512, 512, 3)
./three/data//354_69.npy
(512, 512)
maskpath ./three/labe

67
(512, 512, 3)
./three/data//355_67.npy
(512, 512)
maskpath ./three/label//355_67.npy
68
(512, 512, 3)
./three/data//355_68.npy
(512, 512)
maskpath ./three/label//355_68.npy
69
(512, 512, 3)
./three/data//355_69.npy
(512, 512)
maskpath ./three/label//355_69.npy
70
(512, 512, 3)
./three/data//355_70.npy
(512, 512)
maskpath ./three/label//355_70.npy
71
(512, 512, 3)
./three/data//355_71.npy
(512, 512)
maskpath ./three/label//355_71.npy
72
(512, 512, 3)
./three/data//355_72.npy
(512, 512)
maskpath ./three/label//355_72.npy
73
(512, 512, 3)
./three/data//355_73.npy
(512, 512)
maskpath ./three/label//355_73.npy
74
(512, 512, 3)
./three/data//355_74.npy
(512, 512)
maskpath ./three/label//355_74.npy
75
(512, 512, 3)
./three/data//355_75.npy
(512, 512)
maskpath ./three/label//355_75.npy
76
(512, 512, 3)
./three/data//355_76.npy
(512, 512)
maskpath ./three/label//355_76.npy
77
(512, 512, 3)
./three/data//355_77.npy
(512, 512)
maskpath ./three/label//355_77.npy
78
(512, 512, 3)
./three/data//3

(512, 512, 3)
./three/data//356_82.npy
(512, 512)
maskpath ./three/label//356_82.npy
83
(512, 512, 3)
./three/data//356_83.npy
(512, 512)
maskpath ./three/label//356_83.npy
84
(512, 512, 3)
./three/data//356_84.npy
(512, 512)
maskpath ./three/label//356_84.npy
85
(512, 512, 3)
./three/data//356_85.npy
(512, 512)
maskpath ./three/label//356_85.npy
86
(512, 512, 3)
./three/data//356_86.npy
(512, 512)
maskpath ./three/label//356_86.npy
87
(512, 512, 3)
./three/data//356_87.npy
(512, 512)
maskpath ./three/label//356_87.npy
88
(512, 512, 3)
./three/data//356_88.npy
(512, 512)
maskpath ./three/label//356_88.npy
89
(512, 512, 3)
./three/data//356_89.npy
(512, 512)
maskpath ./three/label//356_89.npy
0
(512, 512, 3)
./three/data//357_0.npy
(512, 512)
maskpath ./three/label//357_0.npy
1
(512, 512, 3)
./three/data//357_1.npy
(512, 512)
maskpath ./three/label//357_1.npy
2
(512, 512, 3)
./three/data//357_2.npy
(512, 512)
maskpath ./three/label//357_2.npy
3
(512, 512, 3)
./three/data//357_3.npy
(512

In [ ]:
#一通道叠加
for subsetindex in range(len(pathmri_list)):
    #获取每个病例的四个模态及Mask的路径
    flair_image = pathmri_list[subsetindex]
    mask_image = pathmask_list[subsetindex]
    #获取每个病例的四个模态及Mask数据
    flair_src = sitk.ReadImage(flair_image, sitk.sitkInt16)
    mask = sitk.ReadImage(mask_image, sitk.sitkUInt8)
    print()
    spacing = flair_src.GetSpacing()
    print(spacing)
#     #GetArrayFromImage()可用于将SimpleITK对象转换为ndarray
#     flair_array = sitk.GetArrayFromImage(flair_src)
#     mask_array = sitk.GetArrayFromImage(mask)
#     #对四个模态分别进行标准化,由于它们对比度不同
#     flair_array_nor = normalize(flair_array)
#     for index in range(0,90):
#         if np.max(mask_array[index,:,:]) != 0:
#             ThreeImageArray = cv2.merge([flair_array_nor[index],flair_array_nor[index]])
#             imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
#             np.save(imagepath,ThreeImageArray)
#             maskpath = outputMask_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
#             maskImg = mask_array[index,:,:]
#             np.save(maskpath,maskImg)


print("Done！")
        
    

(0.75, 0.75, 1.0)
(1.03125, 1.03125, 1.0)
(0.75, 0.75, 1.0)
(0.9375, 0.9375, 1.0)
(0.75, 0.75, 1.0)
(0.75, 0.75, 1.0)
(0.75, 0.75, 1.0)
(0.6875, 0.6875, 1.0)
(0.6875, 0.6875, 1.0)
(0.75, 0.75, 1.0)
(0.75, 0.75, 1.0)
(0.75, 0.75, 1.0)
(0.75, 0.75, 1.0)
(1.125, 1.125, 0.8888888955116272)
(0.75, 0.75, 1.0)
(0.9375, 0.9375, 1.0)
(1.03125, 1.03125, 1.0)
(0.6875, 0.6875, 1.0)
(0.75, 0.75, 0.7777777910232544)
(1.03125, 1.03125, 1.0)
(0.6875, 0.6875, 1.0)
(0.75, 0.75, 1.0)
(0.9375, 0.9375, 0.8888888955116272)
(1.03125, 1.03125, 1.0)
(0.9375, 0.9375, 0.8888888955116272)
(1.03125, 1.03125, 1.0)
(0.75, 0.75, 1.0)
(0.75, 0.75, 1.0)
(0.75, 0.75, 0.7777777910232544)
(0.75, 0.75, 0.8888888955116272)
(0.75, 0.75, 1.0)
(0.9375, 0.9375, 0.8888888955116272)
(0.75, 0.75, 1.0)
(0.625, 0.625, 1.7777777910232544)
(0.9375, 0.9375, 0.8888888955116272)
(0.9375, 0.9375, 0.8888888955116272)
(0.75, 0.75, 1.0)
(0.9375, 0.9375, 1.0)
(1.03125, 1.03125, 1.0)
(1.03125, 1.03125, 1.0)
(0.6875, 0.6875, 1.0)
(1.03125, 1.03

In [85]:
#七通道叠加
for subsetindex in range(len(pathmri_list)):
    flair_image = pathmri_list[subsetindex]
    mask_image = pathmask_list[subsetindex]
    #获取每个病例的四个模态及Mask数据
    flair_src = sitk.ReadImage(flair_image, sitk.sitkInt16)
    mask = sitk.ReadImage(mask_image, sitk.sitkUInt8)
    #GetArrayFromImage()可用于将SimpleITK对象转换为ndarray
    flair_array = sitk.GetArrayFromImage(flair_src)
    mask_array = sitk.GetArrayFromImage(mask)
    #对四个模态分别进行标准化,由于它们对比度不同
    flair_array_nor = normalize(flair_array)
    for index in range(0,90):
        index_1 = index - 1
        index_1_2 = index - 2
        index_1_3 = index - 3
        index_2 = index + 1
        index_2_2 = index + 2
        index_2_3 = index + 3
        maskpath = outputMask_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
        maskImg = mask_array[index,:,:]                      
        if (index == 0):
            if np.max(mask_array[index,:,:]) != 0:
                ThreeImageArray = cv2.merge([flair_array_nor[3],flair_array_nor[2],flair_array_nor[1],flair_array_nor[0],flair_array_nor[1],flair_array_nor[2],flair_array_nor[3]])
                imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
                np.save(maskpath,maskImg)
        if (index == 1):
            if np.max(mask_array[index,:,:]) != 0:
                ThreeImageArray = cv2.merge([flair_array_nor[2],flair_array_nor[1],flair_array_nor[0],flair_array_nor[1],flair_array_nor[2],flair_array_nor[3],flair_array_nor[4]])
                imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
                np.save(maskpath,maskImg)
        if (index == 2):
            if np.max(mask_array[index,:,:]) != 0:
                ThreeImageArray = cv2.merge([flair_array_nor[1],flair_array_nor[0],flair_array_nor[1],flair_array_nor[2],flair_array_nor[3],flair_array_nor[4],flair_array_nor[5]])
                imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
                np.save(maskpath,maskImg)
        if (index == 87):
            if np.max(mask_array[index,:,:]) != 0:
                ThreeImageArray = cv2.merge([flair_array_nor[84],flair_array_nor[85],flair_array_nor[86],flair_array_nor[87],flair_array_nor[88],flair_array_nor[89],flair_array_nor[88]])
                imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
                np.save(maskpath,maskImg)
        if (index == 88):
            if np.max(mask_array[index,:,:]) != 0:
                ThreeImageArray = cv2.merge([flair_array_nor[85],flair_array_nor[86],flair_array_nor[87],flair_array_nor[88],flair_array_nor[89],flair_array_nor[88],flair_array_nor[87]])
                imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
                np.save(maskpath,maskImg)
        elif (index == 89):
            if np.max(mask_array[index,:,:]) != 0:
                ThreeImageArray = cv2.merge([flair_array_nor[86],flair_array_nor[87],flair_array_nor[88],flair_array_nor[89],flair_array_nor[88],flair_array_nor[87],flair_array_nor[86]])
                imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
                np.save(maskpath,maskImg)
        else:
            if np.max(mask_array[index,:,:]) != 0:
                ThreeImageArray = cv2.merge([flair_array_nor[index_1_3],flair_array_nor[index_1_2],flair_array_nor[index_1],flair_array_nor[index],flair_array_nor[index_2],flair_array_nor[index_2_2],flair_array_nor[index_2_3]])
                imagepath = outputImg_path + "//" + str(subsetindex) + "_" + str(index) + ".npy"
                np.save(imagepath,ThreeImageArray)#(160,160,4) np.float dtype('float64')
                np.save(maskpath,maskImg)

print("Done！")
        
    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76

65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76

57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76

...

80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76